# Anonymizer

Phone numbers can be anonymized before or after featurization; this workbook walks through both. Additionally, phone number formatting (e.g. expectations about international calling codes having been stripped) can be checked during the anonymization process by passing a format_checker to the anonymizer; this is demonstrated as well. 

In [1]:
from cider.datastore import DataStore
from cider.anonymizer import Anonymizer
from pandas.api.types import is_numeric_dtype

import os
import sys

import pandas as pd

# Prevents python version mismatches between spark driver and executor
os.environ['PYSPARK_PYTHON'] = sys.executable
os.environ['PYSPARK_DRIVER_PYTHON'] = sys.executable

Set up the configuration file and load some simulated data, including featurization results if present, using the datastore.

In [2]:
# This path should point to your cider installation, where configs and data for this demo are located. In particular, this file must
# contain a 
from pathlib import Path
cider_installation_directory = Path('../../cider')

datastore = DataStore(config_file_path_string= cider_installation_directory / 'configs' / 'config_anonymize.yml')
anonymizer = Anonymizer(datastore=datastore)

outputs_path = anonymizer.outputs_path

23/05/24 13:54:44 WARN Utils: Your hostname, MacBook-Pro.local resolves to a loopback address: 127.0.0.1; using 10.0.0.43 instead (on interface en0)
23/05/24 13:54:44 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address


Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).


23/05/24 13:54:45 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


Loading CDR...


Loading recharges...
SUCCESS!
Loading mobile data...
Loading mobile money...


## Anonymize input data

We can anonymize the five main categories of input data which contain phone numbers: 

- CDR (calls and texts)
- Mobile money transactions
- Mobile data transactions
- Recharges
- Labels (e.g. from a ground-truth survey)

It's important to anonymize these using the same anonymization salt, to ensure that all of
a given subscriber's data is indexed by the same obfuscated string.

In [3]:
anonymizer.anonymize_cdr()

anonymized_cdr = pd.read_csv(outputs_path / 'outputs' / 'cdr.csv')
anonymized_cdr.head()

txn_type         caller_id      recipient_id            timestamp  duration  \
0     call  p7OPQLOrvqqYDvVa  1Z7rQb4GO2jXzbpG  2020-01-01 00:00:42     253.0   
1     text  p7OPQLOrVlZYDvVa  AbRlyk74NOBJyqwY  2020-01-01 00:02:04       NaN   
2     text  G5vAyA41G9wqQadO  1xMmQpJkXaVVz9wa  2020-01-01 00:02:12       NaN   
3     call  nVLoQg1drok6zx3Z  KlVDmV2g29mA7Qvq  2020-01-01 00:02:23      96.0   
4     text  bRlykJqR9eAXJQqw  BWvLye4LxnnOQdYG  2020-01-01 00:03:05       NaN   

  caller_antenna recipient_antenna international  
0           a101               a54      domestic  
1            a44              a110      domestic  
2           a145               a96      domestic  
3            a84               a36      domestic  
4           a261              a268      domestic

In [4]:
anonymizer.anonymize_mobilemoney()

anonymized_mobilemoney = pd.read_csv(outputs_path / 'outputs' / 'mobilemoney.csv')
anonymized_mobilemoney.head()

txn_type         caller_id      recipient_id            timestamp  \
0      p2p  LxA7zdJNn8enQbVY  35nJzJZNWkPnz16l  2020-01-01 00:15:51   
1  cashout  LxA7zdJd7rKPQbVY               NaN  2020-01-01 00:18:59   
2   cashin  0vK4yVJnrmaOy71O               NaN  2020-01-01 00:28:17   
3      p2p  O8xoDrk5vX36QEGL  VpAaQawNqaN6ze9q  2020-01-01 00:28:29   
4  cashout  NkZlD88rZN0BDG5J               NaN  2020-01-01 00:31:03   

      amount  sender_balance_before  sender_balance_after  \
0  55.163315              324.21875             269.05542   
1  81.861000              185.57620             103.71520   
2  29.225048               98.63829             127.86334   
3  45.561913              248.71838             203.15646   
4  55.040770              150.88644              95.84567   

   recipient_balance_before  recipient_balance_after  
0                 112.54498                167.70830  
1                       NaN                      NaN  
2                       NaN                      NaN  
3                 212.01639                257.57828  
4                       NaN                      NaN

In [5]:
anonymizer.anonymize_mobiledata()

anonymized_mobiledata = pd.read_csv(outputs_path / 'outputs' / 'mobiledata.csv')
anonymized_mobiledata.head()

caller_id     volume            timestamp
0  mpLEyMkZWmNdDqvN   91.38652  2020-01-01 00:01:15
1  NkZlD88rvpbZDG5J  118.89835  2020-01-01 00:02:27
2  BWvLye4EgqAWQdYG   67.68214  2020-01-01 00:16:33
3  WvLyem297x9l6ydY   65.52507  2020-01-01 00:23:37
4  nVLoQg1drok6zx3Z   99.46138  2020-01-01 00:41:44

In [6]:
anonymizer.anonymize_recharges()

anonymized_recharges = pd.read_csv(outputs_path / 'outputs' / 'recharges.csv')
anonymized_recharges.head()

caller_id  amount            timestamp
0  6aA9yvnL0o61yJMY    96.0  2020-01-01 00:02:47
1  1xMmQpJ74bMkz9wa    73.0  2020-01-01 00:04:33
2  AbRlyk74R1YJyqwY    98.0  2020-01-01 00:08:36
3  1xMmQpJk8ALoz9wa     7.0  2020-01-01 00:14:37
4  1Z7rQb4Nbo1vzbpG    76.0  2020-01-01 00:24:36

In [7]:
anonymizer.anonymize_labels()

anonymized_labels = pd.read_csv(outputs_path / 'outputs' / 'labels.csv')
anonymized_labels.head()

name  label     weight
0  BKGnyZoaegLxz9Za  18760   3.711266
1  6aA9yvnL8aqOyJMY  21897  69.385541
2  Bj0nDOWV1VNbDK2O  20663  67.035003
3  eALxDXe0WKplQdlp  19756  43.047178
4  p7OPQLOYpMKXDvVa  19978  76.778898

In [8]:
raw_cdr_file = pd.read_csv(datastore.cfg.path.input_data.file_paths.cdr)
raw_recharges_file = pd.read_csv(datastore.cfg.path.input_data.file_paths.recharges)
raw_mobiledata_file = pd.read_csv(datastore.cfg.path.input_data.file_paths.mobiledata)
raw_mobilemoney_file = pd.read_csv(datastore.cfg.path.input_data.file_paths.mobilemoney)
raw_labels_file = pd.read_csv(datastore.cfg.path.input_data.file_paths.labels)

## Anonymize features

We can also anonymize featurized data. **This is not necessary (nor will it work) if the features are computed using already-anonymized data.**

In [9]:
anonymizer.anonymize_features()
anonymized_features = pd.read_csv(outputs_path / 'outputs' / 'features.csv')
anonymized_features.head()

name  active_days_allweek_allday  active_days_allweek_day  \
0  xMmQpj25daOLRz9w                          54                       46   
1  Na6Q4xNdBX5RdQxw                          56                       51   
2  nGeQjv2jeVrRBQXW                          57                       45   
3  5vAyA0NZP6oZ6Qad                          54                       47   
4  pLEyMlebKR37oQqv                          53                       41   

   active_days_allweek_night  active_days_weekday_allday  \
0                         46                          38   
1                         44                          41   
2                         45                          41   
3                         46                          40   
4                         44                          39   

   active_days_weekday_day  active_days_weekday_night  \
0                       33                         32   
1                       36                         32   
2                       34                         32   
3                       35                         33   
4                       31                         33   

   active_days_weekend_allday  active_days_weekend_day  \
0                          16                       13   
1                          15                       15   
2                          16                       11   
3                          14                       12   
4                          14                       10   

   active_days_weekend_night  ...  mobilemoney_outgoing_p2p_amount_min  \
0                         14  ...                            30.222473   
1                         12  ...                                  NaN   
2                         13  ...                            32.282750   
3                         13  ...                                  NaN   
4                         11  ...                            43.527973   

   mobilemoney_outgoing_p2p_amount_max  \
0                            70.803710   
1                                  NaN   
2                            66.296750   
3                                  NaN   
4                            63.519386   

   mobilemoney_outgoing_p2p_balance_before_mean  \
0                                    206.221286   
1                                           NaN   
2                                    194.259438   
3                                           NaN   
4                                    191.142494   

   mobilemoney_outgoing_p2p_balance_before_min  \
0                                    180.20338   
1                                          NaN   
2                                    136.78952   
3                                          NaN   
4                                    132.54959   

   mobilemoney_outgoing_p2p_balance_before_max  \
0                                    239.67809   
1                                          NaN   
2                                    285.25427   
3                                          NaN   
4                                    297.36365   

   mobilemoney_outgoing_p2p_balance_after_mean  \
0                                   158.092635   
1                                          NaN   
2                                   147.203631   
3                                          NaN   
4                                   138.052689   

   mobilemoney_outgoing_p2p_balance_after_min  \
0                                   109.39968   
1                                         NaN   
2                                    70.49276   
3                                         NaN   
4                                    69.03021   

   mobilemoney_outgoing_p2p_balance_after_max  mobilemoney_outgoing_p2p_txns  \
0                                   185.19756                            6.0   
1                                         NaN                            NaN   
2                                   252.97151                 

## Use a custom format checker

It is a good idea to check the format of numbers as you anonymize them to make sure they have been processed according to expectations. Because the anonymizer uses a hash function, similar numbers will *not* result in similar anonymized strings. For example, the numbers 1234567, 01234567, and 880 1234567 will all result in completely different anonymized strings.

The Anonymizer object accepts a format checker when it's constructed. The checker will be evaluated on inputs as strings, and should return `True` if the format is acceptable and `False` if not.

Anonymization will fail if any number fails this check. So we encourage you to clean your data prior to passing it through this step. 

This demo is based on a simplified version of Bangladesh's [mobile phone number format](https://en.wikipedia.org/wiki/Telephone_numbers_in_Bangladesh). We're assuming that leading "0", "880", and "+" are removed, which means all numbers will be ten digits and will not start with "0".

It's important to be consistent in how phone numbers are provided. For example, if a number is represented differently based on where the call is dialed from, it's necessary to normalize: Perhaps by stripping the country code and also the domestic prefix (here '0'), and by stripping the operator prefix. The anonymizer does not intelligently map two representations of the same number to the same string. Cider expects information about whether calls/texts are domestic or international to be provided. So it's likely users will already have checked number prefixes, and perhaps removed them.

In [10]:
def is_valid_mobile_number(x):
    if any(c.isdigit() == False for c in x):
        print(x, " has non-numeric characters. Please remove these.")
        return False
    if x[0] == "0":
        print(x, "starts with 0. Please strip leading zeros from numbers.")
        return False
    sl = len(x)
    if sl != 10:
        print("Valid numbers have ten digits;", x, "has", sl)
        return False
    return True

anonymizer_with_check = Anonymizer(datastore=datastore, format_checker=is_valid_mobile_number)

Loading CDR...
Loading recharges...
SUCCESS!
Loading mobile data...
Loading mobile money...


The synthetic data we are working with has not been processed to remove leading "880"s, "0"s, or "+"s, so when we try to anonymize the CDR data, an error is raised notifying the user that phone numbers haven't been processed as expected.

In [11]:
print(datastore.cdr.toPandas().head())
anonymizer_with_check.anonymize_cdr()

/Users/mlevy/miniconda3/envs/myenv_x86/lib/python3.8/site-packages/pyspark/sql/pandas/conversion.py:248: FutureWarning: Passing unit-less datetime64 dtype to .astype is deprecated and will raise in a future version. Pass 'datetime64[ns]' instead
  series = series.astype(t, copy=False)
/Users/mlevy/miniconda3/envs/myenv_x86/lib/python3.8/site-packages/pyspark/sql/pandas/conversion.py:248: FutureWarning: Passing unit-less datetime64 dtype to .astype is deprecated and will raise in a future version. Pass 'datetime64[ns]' instead
  series = series.astype(t, copy=False)


  txn_type       caller_id    recipient_id           timestamp  duration  \
0     call     00180479117     00186879451 2020-01-01 00:00:42     253.0   
1     text     00181616517     00185633871 2020-01-01 00:02:04       NaN   
2     text     00189653293     00186624501 2020-01-01 00:02:12       NaN   
3     call     00183331706  +8800186773263 2020-01-01 00:02:23      96.0   
4     text  +8800189721427     00188688509 2020-01-01 00:03:05       NaN   

  caller_antenna recipient_antenna international        day  
0           a101               a54      domestic 2020-01-01  
1            a44              a110      domestic 2020-01-01  
2           a145               a96      domestic 2020-01-01  
3            a84               a36      domestic 2020-01-01  
4           a261              a268      domestic 2020-01-01  


Valid numbers have ten digits; 8800180789080 has 13
00180479117 starts with 0. Please strip leading zeros from numbers.


23/05/24 13:55:20 ERROR Executor: Exception in task 0.0 in stage 49.0 (TID 45)
org.apache.spark.api.python.PythonException: Traceback (most recent call last):
  File "/Users/mlevy/Dropbox/professional/givedirectly/cider/cider/anonymizer.py", line 142, in <lambda>
    lambda raw: Anonymizer._check_identifier_format_and_hash(raw, encoder, format_checker), StringType()
  File "/Users/mlevy/Dropbox/professional/givedirectly/cider/cider/anonymizer.py", line 197, in _check_identifier_format_and_hash
    raise ValueError(f'Bad input to anonymization: {raw_string} rejected by provided format format_checker.')
ValueError: Bad input to anonymization: 00180479117 rejected by provided format format_checker.

	at org.apache.spark.api.python.BasePythonRunner$ReaderIterator.handlePythonException(PythonRunner.scala:552)
	at org.apache.spark.sql.execution.python.PythonUDFRunner$$anon$2.read(PythonUDFRunner.scala:86)
	at org.apache.spark.sql.execution.python.PythonUDFRunner$$anon$2.read(PythonUDFRunner.

PythonException: 
  An exception was thrown from the Python worker. Please see the stack trace below.
Traceback (most recent call last):
  File "/Users/mlevy/Dropbox/professional/givedirectly/cider/cider/anonymizer.py", line 142, in <lambda>
    lambda raw: Anonymizer._check_identifier_format_and_hash(raw, encoder, format_checker), StringType()
  File "/Users/mlevy/Dropbox/professional/givedirectly/cider/cider/anonymizer.py", line 197, in _check_identifier_format_and_hash
    raise ValueError(f'Bad input to anonymization: {raw_string} rejected by provided format format_checker.')
ValueError: Bad input to anonymization: 00180479117 rejected by provided format format_checker.
